In [106]:
import networkx as nx
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import numpy as np

In [113]:
def plot_causal_graph(adj_matrix, factor_list, results_serial):
    """
    Plot the CPDAG using pairwise correlations taken from results_serial
    *only* for entries with no conditioning set (sub_z == []).
    
    - Edge color encodes sign of the stored correlation.
    - Edge width scales with |corr|.
    - Arrow for one-way edges; line-style for symmetric (undirected) edges.
    - If a needed (i,j) pair has no no-sub_z entry, it is drawn in gray with 'n/a'.
    """
    nodes = factor_list

    # Build a lookup: undirected key -> correlation
    # Use frozenset({i,j}) so (i,j) and (j,i) map to the same value
    corr_map = {}
    for i, j, sub_z, corr, p_value in results_serial:
        if not sub_z:  # no conditioning variables
            key = frozenset((i, j))
            # Keep the first encountered value; or overwrite if you prefer last-seen
            if key not in corr_map:
                corr_map[key] = corr

    G = nx.DiGraph()
    edge_info = []
    edge_labels = {}

    # Add edges from adjacency matrix and attach style from corr_map
    for i in range(len(nodes)):
        for j in range(len(nodes)):
            if adj_matrix[i, j] != 0:
                node_i = nodes[i]
                node_j = nodes[j]
                key = frozenset((i, j))
                pcorr = corr_map.get(key, np.nan)

                if np.isnan(pcorr):
                    edge_color = '#B0B0B0'  # fallback when no no-sub_z corr available
                    edge_width = 1.5
                    label = 'n/a'
                    weight = 0.0
                else:
                    edge_color = '#F2C14E' if pcorr > 0 else '#8e7dbe'
                    edge_width = 1 + 2 * abs(pcorr)
                    label = f"{pcorr:+.2f}"
                    weight = pcorr

                G.add_edge(node_i, node_j, weight=weight)
                edge_info.append((node_i, node_j, edge_color, edge_width))
                edge_labels[(node_i, node_j)] = label

    # Layout & node draw
    pos = nx.circular_layout(G)
    label_pos = {n: (p[0] * 1.2, p[1] * 1.2) for n, p in pos.items()}

    plt.figure(figsize=(11, 11), dpi=900)
    nx.draw_networkx_nodes(
        G, pos,
        node_color=['#C9BFE1'],
        edgecolors='white',
        node_size=500,
        alpha=0.9
    )
    nx.draw_networkx_labels(G, label_pos, font_size=16, font_family="arial", font_color='black')

    # Draw edges (merge symmetric pairs into undirected style)
    handled = set()
    for u, v, color, width in edge_info:
        if (v, u) in handled:
            continue
        arc_rad = 0.1
        if G.has_edge(v, u):
            # symmetric → draw as undirected line
            nx.draw_networkx_edges(
                G, pos, edgelist=[(u, v)], width=width, edge_color=color,
                arrowstyle='-', arrowsize=20, connectionstyle=f'arc3,rad={arc_rad}',
                min_source_margin=20, min_target_margin=20
            )
            handled.add((u, v))
        else:
            # one-way → directed arrow
            nx.draw_networkx_edges(
                G, pos, edgelist=[(u, v)], width=width, edge_color=color,
                arrowstyle='simple', arrowsize=20, connectionstyle=f'arc3,rad={arc_rad}',
                min_source_margin=20, min_target_margin=20
            )
            handled.add((u, v))

    # Edge labels
    nx.draw_networkx_edge_labels(
        G, pos,
        edge_labels=edge_labels,
        font_size=14,
        font_color='black',
        font_family="arial",
        rotate=True,
        label_pos=0.5,
        bbox=dict(facecolor='none', edgecolor='none', pad=0)
    )

    # Legend
    pos_patch = mpatches.Patch(color='#F2C14E', label='Positive (pairwise)')
    neg_patch = mpatches.Patch(color='#8e7dbe', label='Negative (pairwise)')
    plt.legend(handles=[pos_patch, neg_patch], loc='lower left', fontsize=14, frameon=False)

    plt.gca().margins(x=0.3, y=0.3)
    plt.axis('off')
    plt.show()

In [ ]:
import pandas as pd
from pc_gcastle import PC
from random import shuffle

def run_pc_analysis(df, factor_list, alpha=0.05, shuffle_factors=False, ci_test='spearman'):
    """
    Run PC algorithm for a selected subset of factors.
    
    Parameters:
        df (pd.DataFrame): Original dataframe containing 'factor', 'cbsacode', and 'SSAMI'.
        factor_list (list): List of factor names to include in the analysis.
        alpha (float): Significance level for conditional independence tests.
        shuffle_factors (bool): Whether to shuffle the factor list randomly.
    
    Returns:
        pc (PC object): The trained PC model.
    """
    
    if shuffle_factors:
        shuffle(factor_list)
        print(factor_list)
    
    # Filter and pivot
    df_select = df.loc[df['factor'].isin(factor_list)]

    dfp = df_select.pivot(index=["cbsacode"], columns="factor", values='FsAMI').reset_index()
    # Reorder columns explicitly to match shuffled factor_list
    dfp = dfp[['cbsacode'] + factor_list]
    # Drop missing values and isolate data matrix
    df_cleaned = dfp.drop(columns=["cbsacode"]).dropna()
    data_matrix = df_cleaned.to_numpy()

    # Run PC algorithm
    pc = PC(alpha=alpha, ci_test = ci_test)
    pc.learn(data_matrix, columns=factor_list)
    
    print("Learned skeleton (CPDAG):")
    plot_causal_graph(pc.causal_matrix, factor_list, pc._results)
    
    return pc._results

In [227]:
from collections import defaultdict
import numpy as np
import pandas as pd
from random import shuffle

def run_pc_with_stability(df, factor_list, alpha=0.01, ci_test='spearman',
                          n_runs=100, stability_threshold=0.8, verbose=True):
    """
    Run PC multiple times with shuffled factor orders and return stable directed edges.
    
    Returns:
        stable_adj (np.ndarray): binary adjacency matrix of stable directed edges (i → j)
        edge_freq_df (pd.DataFrame): DataFrame of all edge frequencies (from, to, freq)
        final_pc._results (list): Last PC _results for plotting
    """
    # Step 1: Store edge frequencies as (from_name, to_name) → count
    edge_count_dict = defaultdict(int)
    final_pc = None

    for run in range(n_runs):
        # Step 2: Shuffle factor order
        shuffled = factor_list.copy()
        shuffle(shuffled)

        # Step 3: Pivot and reorder columns to match shuffled
        df_sub = df[df['factor'].isin(shuffled)]
        dfp = df_sub.pivot(index="cbsacode", columns="factor", values="FsAMI").reset_index()
        dfp = dfp[['cbsacode'] + shuffled]
        df_cleaned = dfp.drop(columns=["cbsacode"]).dropna()
        data_matrix = df_cleaned.to_numpy()

        # Step 4: Run PC
        pc = PC(alpha=alpha, ci_test=ci_test)
        pc.learn(data_matrix, columns=shuffled)

        var_names = pc.causal_matrix.index.tolist()

        # Step 5: Record directed edges (i → j) using actual var names
        cm = np.array(pc.causal_matrix)
        var_names = pc.causal_matrix.columns  # Tensor

        for i, from_var in enumerate(var_names):
            for j, to_var in enumerate(var_names):
                if cm[i, j] == 1:
                    edge_count_dict[(from_var, to_var)] += 1

        final_pc = pc
        if verbose:
            print(f"Run {run+1}/{n_runs} complete.")

    # Step 6: Compute frequency for all possible directed edges
    all_edges = [(a, b) for a in factor_list for b in factor_list if a != b]
    edge_freq_df = pd.DataFrame([
        {"from": a, "to": b, "freq": edge_count_dict[(a, b)] / n_runs}
        for (a, b) in all_edges
    ])

    # Step 7: Build adjacency matrix with same order as factor_list
    var_idx = {v: i for i, v in enumerate(factor_list)}
    stable_adj = np.zeros((len(factor_list), len(factor_list)), dtype=int)

    for _, row in edge_freq_df.iterrows():
        if row["freq"] >= stability_threshold:
            i = var_idx[row["from"]]
            j = var_idx[row["to"]]
            stable_adj[i, j] = 1

    # Step 8: Plot and return
    print("Stable CPDAG from shuffled PC runs:")
    plot_causal_graph(stable_adj, factor_list, final_pc._results)

    return stable_adj, edge_freq_df, final_pc._results

In [184]:
#df = pd.read_csv('../00_data/14_output/FsAMIs_8_10.csv')
#df = pd.read_csv('../00_data/14_output/FsAMIs_0902_density.csv')
#df = pd.read_csv('../00_data/14_output/FsAMIs_0902_pop.csv')
df = pd.read_csv('../00_data/14_output/FsAMIs_0903_pop_ko.csv')

In [ ]:
df

In [185]:
df['factor'].unique()

array(['BINGE', 'CSMOKING', 'DEPRESSION', 'DIABETES', 'LPA', 'OBESITY',
       'adult_smoking', 'adult_obesity', 'excessive_drinking',
       'diabetes_prevalence', 'some_college', 'unemployment',
       'children_single_parent', 'mental_health_providers',
       'median_household_income', 'driving_alone_to_work', 'sti', 'FFR20',
       'gdp', 'coverage_50', 'coverage_60', 'coverage_70', 'coverage_80',
       'coverage_90', 'noise50n', 'noise60n', 'noise70n', 'noise80n',
       'noise90n', 'Park_Area_Acres'], dtype=object)

## PCA

In [186]:
df.columns

Index(['cbsacode', 'factor', 'best_k', 'baseline_moran_value',
       'baseline_moran_p', 'final_moran_value', 'final_moran_p',
       'selected_m_eigs', 'FsAMI', 'beta', 'p_value', 'CI_lower', 'CI_upper',
       'AIC'],
      dtype='object')

In [190]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

pca_factors = ['DIABETES', 'OBESITY', 'BINGE', 'CSMOKING', 'LPA']
cols_to_use = ['cbsacode'] + pca_factors
filtered_df = df[df['factor'].isin(pca_factors)]
pca_wide = filtered_df.pivot_table(index='cbsacode', columns='factor', values='FsAMI')


# Standardize FsAMI values
scaler = StandardScaler()
X_scaled = scaler.fit_transform(pca_wide[pca_factors])

# Run PCA
pca = PCA()
X_pca = pca.fit_transform(X_scaled)

# Append to original df
pc1_scores = X_pca[:, 0]
cbsacodes = pca_wide.index

pca_result_df = pd.DataFrame({
    'cbsacode': cbsacodes,
    'factor': 'PCA',              # tag new synthetic variable
    'FsAMI': pc1_scores           # PC1 values as SAMI-like scores
})

for col in ['best_k', 'baseline_moran_value', 'baseline_moran_p',
            'final_moran_value', 'final_moran_p', 'selected_m_eigs',
            'beta', 'p_value', 'CI_lower', 'CI_upper', 'AIC']:
    pca_result_df[col] = None

df_with_pca = pd.concat([df, pca_result_df], ignore_index=True)

/var/folders/xn/k3tchqyx5bn081b3tlx0k4940000gn/T/ipykernel_1898/3856362319.py:33: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_with_pca = pd.concat([df, pca_result_df], ignore_index=True)


In [191]:
my_factors = ['gdp','mental_health_providers','coverage_50','DEPRESSION','Park_Area_Acres','FFR20','PCA']

## VIF

In [192]:
import pandas as pd
from statsmodels.stats.outliers_influence import variance_inflation_factor
import statsmodels.api as sm

filtered_df = df_with_pca[df_with_pca['factor'].isin(my_factors)]
fsmis_wide = filtered_df.pivot_table(index='cbsacode', columns='factor', values='FsAMI')


fsmis_clean = fsmis_wide.dropna()
X = sm.add_constant(fsmis_clean)

vif_data = pd.DataFrame({
    "factor": X.columns,
    "VIF": [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
})


# Display VIF
print(vif_data)

                    factor       VIF
0                    const  1.001732
1               DEPRESSION  1.054780
2                    FFR20  1.136764
3                      PCA  1.128824
4          Park_Area_Acres  1.013478
5              coverage_50  1.044113
6                      gdp  1.161934
7  mental_health_providers  1.053107


In [155]:
# k=5
pc_result= run_pc_analysis(df, factor_list=my_factors, alpha=0.05, shuffle_factors=False,ci_test='spearman')

[(0, 1, [], -0.14878271878378635, 2.5322884529014828e-05), (0, 2, [], 0.08419453381158919, 0.017577053308091225), (0, 3, [], 0.08296835634854086, 0.01929878570556008), (0, 4, [], -0.14707946366498145, 3.138862176067142e-05), (0, 5, [], 0.037002965495220023, 0.2973924881386111), (0, 6, [], 0.24389317434566013, 3.1364355446686907e-12), (0, 7, [], -0.13092158668920859, 0.00021427239813801808), (1, 2, [], -0.15006810106805113, 2.1500859585017227e-05), (1, 3, [], 0.1355545132152851, 0.0001262018201004241), (1, 4, [], 0.03369492297760845, 0.34270810466963264), (1, 5, [], -0.15719615615265625, 8.467812949874116e-06), (1, 6, [], -0.1006151903952059, 0.004516089561061692), (1, 7, [], 0.6036224561809093, 4.402331901434056e-80), (2, 3, [], -0.014756473303258844, 0.6778215153210341), (2, 4, [], 0.10542410737208689, 0.002919099141567566), (2, 5, [], 0.009179231072906474, 0.796087829795899), (2, 6, [], 0.1601220780008593, 5.707043308983304e-06), (2, 7, [], -0.11755058740305778, 0.000897821724561519)

In [157]:
# k=6
pc_result= run_pc_analysis(df, factor_list=my_factors, alpha=0.05, shuffle_factors=True,ci_test='spearman')

['Park_Area_Acres', 'coverage_50', 'OBESITY', 'DEPRESSION', 'mental_health_providers', 'FFR20', 'gdp', 'LPA']
[(0, 1, [], -0.009392358876269088, 0.791461163999734), (0, 2, [], -0.1303665564168927, 0.00022804035458349046), (0, 3, [], -0.025424136031137103, 0.47409002141454004), (0, 4, [], 0.008334863806222786, 0.814486617280278), (0, 5, [], -0.01565514947008222, 0.6594004671819489), (0, 6, [], 0.06981619279325194, 0.04908832192007985), (0, 7, [], -0.137273841284747, 0.00010324195403145324), (1, 2, [], 0.07912603748747062, 0.025680737904655013), (1, 3, [], -0.027984177338381464, 0.4307274118521308), (1, 4, [], -0.003607362414467662, 0.9191118378372464), (1, 5, [], 0.06093207828983805, 0.0859942371620267), (1, 6, [], 0.10743709517598928, 0.0024190614123667468), (1, 7, [], 0.1506306782235879, 2.0006544467278322e-05), (2, 3, [], 0.1673296380672432, 2.094908882781779e-06), (2, 4, [], -0.14022486368442183, 7.274029666976593e-05), (2, 5, [], -0.13184075407692902, 0.00019317178094904375), (2, 6

In [183]:
# k=6 pca
pc_result= run_pc_analysis(df_with_pca, factor_list=my_factors, alpha=0.05, shuffle_factors=False,ci_test='spearman')

[(0, 1, [], 0.09994960783672174, 0.004790621445343404), (0, 2, [], 0.10743709517598928, 0.0024190614123667468), (0, 3, [], -0.12374753382902344, 0.00047032134445598023), (0, 4, [], 0.06981619279325194, 0.04908832192007985), (0, 5, [], 0.2650914856588919, 2.983064907619592e-14), (0, 6, [], -0.2127399747657063, 1.3747637715759405e-09), (1, 2, [], -0.003607362414467662, 0.9191118378372464), (1, 3, [], 0.1367698718868808, 0.00010952805307503758), (1, 4, [], 0.008334863806222786, 0.814486617280278), (1, 5, [], 0.23597183675136288, 1.6023369156888765e-11), (1, 6, [], -0.17272116965226303, 9.622512794216791e-07), (2, 3, [], -0.027984177338381464, 0.4307274118521308), (2, 4, [], -0.009392358876269088, 0.791461163999734), (2, 5, [], 0.06093207828983805, 0.0859942371620267), (2, 6, [], 0.13436970031470025, 0.00014473252836904804), (3, 4, [], -0.025424136031137103, 0.47409002141454004), (3, 5, [], 0.020012614758598852, 0.5731358935148028), (3, 6, [], 0.10385094045867377, 0.0033735427305713202), (

In [218]:
# k optimize pca
pc_result= run_pc_analysis(df_with_pca, factor_list=my_factors, alpha=0.05, shuffle_factors=True,ci_test='spearman')

['PCA', 'mental_health_providers', 'FFR20', 'gdp', 'coverage_50', 'DEPRESSION', 'Park_Area_Acres']
[(0, 1, [], -0.10709564647533087, 0.002497947054168009), (0, 2, [], -0.1515425614360477, 1.7792053950031927e-05), (0, 3, [], -0.1807354103343102, 2.8934661863161685e-07), (0, 4, [], 0.14139412905027013, 6.319414897664468e-05), (0, 5, [], 0.10407935308881272, 0.0033037981365251117), (0, 6, [], -0.10698533301458102, 0.0025239306891946213), (1, 2, [], 0.2011896849391198, 1.0504280743334763e-08), (1, 3, [], 0.04761942405339755, 0.1798187057275704), (1, 4, [], -0.03637155885410609, 0.3057179357382316), (1, 5, [], 0.0960019669661458, 0.006751751931313912), (1, 6, [], -0.03862072111424477, 0.27675744072699243), (2, 3, [], 0.2705027442234699, 8.48284182621357e-15), (2, 4, [], 0.0464999299047397, 0.19028188338887578), (2, 5, [], 0.009180043079328968, 0.7960701887301179), (2, 6, [], 0.017768348419536967, 0.6169039787993169), (3, 4, [], 0.10016130268757407, 0.004701711735058681), (3, 5, [], -0.15860

In [232]:
# k optimize pca
pc_result= run_pc_with_stability(df_with_pca, my_factors, alpha=0.05, ci_test='spearman',
                          n_runs=100, stability_threshold=0.5, verbose=True)

Run 1/100 complete.
Run 2/100 complete.
Run 3/100 complete.
Run 4/100 complete.
Run 5/100 complete.
Run 6/100 complete.
Run 7/100 complete.
Run 8/100 complete.
Run 9/100 complete.
Run 10/100 complete.
Run 11/100 complete.
Run 12/100 complete.
Run 13/100 complete.
Run 14/100 complete.
Run 15/100 complete.
Run 16/100 complete.
Run 17/100 complete.
Run 18/100 complete.
Run 19/100 complete.
Run 20/100 complete.
Run 21/100 complete.
Run 22/100 complete.
Run 23/100 complete.
Run 24/100 complete.
Run 25/100 complete.
Run 26/100 complete.
Run 27/100 complete.
Run 28/100 complete.
Run 29/100 complete.
Run 30/100 complete.
Run 31/100 complete.
Run 32/100 complete.
Run 33/100 complete.
Run 34/100 complete.
Run 35/100 complete.
Run 36/100 complete.
Run 37/100 complete.
Run 38/100 complete.
Run 39/100 complete.
Run 40/100 complete.
Run 41/100 complete.
Run 42/100 complete.
Run 43/100 complete.
Run 44/100 complete.
Run 45/100 complete.
Run 46/100 complete.
Run 47/100 complete.
Run 48/100 complete.
R

In [233]:
pc_result

(array([[0, 0, 0, 0, 0, 0, 0],
        [1, 0, 0, 0, 0, 0, 0],
        [1, 1, 0, 1, 0, 0, 0],
        [1, 0, 0, 0, 0, 0, 0],
        [1, 0, 0, 1, 0, 0, 0],
        [1, 1, 0, 1, 0, 0, 0],
        [1, 0, 0, 0, 0, 0, 0]]),
                        from                       to  freq
 0                       PCA  mental_health_providers  0.00
 1                       PCA                    FFR20  0.00
 2                       PCA                      gdp  0.00
 3                       PCA              coverage_50  0.00
 4                       PCA               DEPRESSION  0.00
 5                       PCA          Park_Area_Acres  0.00
 6   mental_health_providers                      PCA  1.00
 7   mental_health_providers                    FFR20  0.44
 8   mental_health_providers                      gdp  0.00
 9   mental_health_providers              coverage_50  0.00
 10  mental_health_providers               DEPRESSION  0.44
 11  mental_health_providers          Park_Area_Acres  0.00
 

---

In [93]:
pc_result

[(0, 1, [], 0.08387585728103315, 0.013120325232337126),
 (0, 2, [], -0.0362781539235808, 0.2840225937646408),
 (0, 3, [], -0.037732709182189, 0.26514579927105764),
 (0, 4, [], -0.1335879816079868, 7.449806458659463e-05),
 (0, 5, [], 0.1354227253476587, 5.9105360704461706e-05),
 (1, 2, [], -0.1477015263393805, 1.1631018015785462e-05),
 (1, 3, [], 0.12792989196433485, 0.00014929830133565474),
 (1, 4, [], -0.16623914784720656, 7.732430997741241e-07),
 (1, 5, [], -0.1663525285648006, 7.597962544349789e-07),
 (2, 3, [], -0.005056702716001118, 0.8813320712949012),
 (2, 4, [], 0.061749919397327914, 0.06805053178796268),
 (2, 5, [], 0.0037378879740813265, 0.9121339828460368),
 (3, 4, [], 0.11216017632606842, 0.0008950713736184095),
 (3, 5, [], 0.00013948811967165784, 0.9967144370869179),
 (4, 5, [], 0.08066435025259248, 0.01707008785632149),
 (0, 1, [4], 0.06735094122576725, 0.04653149313893904),
 (0, 1, [5], 0.10974050096105346, 0.0011561290487762906),
 (0, 4, [1], -0.12943849538683103, 0.000

In [ ]:
records = []
for (x_idx, y_idx,cond_indices,corr, p_val ) in pc_result:
    # Convert x_idx and y_idx to factor names:
    x_name = my_factors[x_idx]
    y_name = my_factors[y_idx]
    # Convert conditioning indices (if any) to factor names:
    cond_names = [my_factors[z] for z in cond_indices]

    records.append({
        "X": x_name,
        "Y": y_name,
        "Z":  cond_names,
        "Spearman":corr,
        "p value": p_val
    })

df = pd.DataFrame(records)


In [ ]:
df.to_csv("../00_data/04_output/sasami_result.csv",index=False)

In [ ]:
import pandas as pd
import ast

# Load your CSV
df = pd.read_csv("../00_data/04_output/sasami_result.csv")


# Clean Z column
def clean_z(z):
    try:
        items = ast.literal_eval(z)
        if isinstance(items, list) and len(items) == 0:
            return '-'
        elif isinstance(items, list):
            return ', '.join(str(i) for i in items)
    except:
        return z
    return z

# Apply formatting
df['Z'] = df['Z'].apply(clean_z)
df['Spearman'] = df['Spearman'].astype(float).apply(lambda x: f"{x:.2f}")
df['p value'] = df['p value'].astype(float).apply(lambda x: r"\textless{} 0.001" if x < 0.001 else f"{x:.3f}")

# Split side by side
half = len(df) // 2 + len(df) % 2
df1 = df.iloc[:half].reset_index(drop=True)
df2 = df.iloc[half:].reset_index(drop=True)
combined = pd.concat([df1, df2], axis=1)
combined.columns = ['X', 'Y', 'Z', 'Spearman', 'p value', 'X', 'Y', 'Z', 'Spearman', 'p value']

# Export to LaTeX
latex_code = combined.to_latex(
    index=False,
    column_format="|l|l|l|r|r||l|l|l|r|r|",
    escape=False
)

In [ ]:
with open("sasami_table_final.tex", "w") as f:
    f.write(latex_code)

# 72 * 12

In [ ]:
#df = pd.read_csv('../00_data/14_output/FsAMIs_72.csv')
df = pd.read_csv('../00_data/14_output/SASAMIs_72.csv')


In [ ]:
df.loc[df['factor'] == 'Park_Area_Acres', 'factor'] = 'PARK'
df.loc[df['factor'] == 'noise90n', 'factor'] = 'NOI'
df.loc[df['factor'] == 'no_time_activity', 'factor'] = 'PI'
df.loc[df['factor'] == 'smo_obe_dia', 'factor'] = 'UNH'
df.loc[df['factor'] == 'depressed', 'factor'] = 'DEP'
df.loc[df['factor'] == 'gdp', 'factor'] = 'GDP'
df.loc[df['factor'] == 'mental_health_providers', 'factor'] = 'MHP'

In [ ]:
df.loc[df['cbsacode']==10740]['Year'].unique()

array([2011., 2012., 2013., 2014., 2015., 2016., 2017., 2018., 2019.,
       2020., 2021., 2022.])

In [ ]:

df

cbsacode    Year              factor  baseline_moran_value  \
0       10740.0  2011.0  excessive_drinking              0.082131   
1       11260.0  2011.0  excessive_drinking              0.082131   
2       12060.0  2011.0  excessive_drinking              0.082131   
3       12260.0  2011.0  excessive_drinking              0.082131   
4       12420.0  2011.0  excessive_drinking              0.082131   
...         ...     ...                 ...                   ...   
17275   45820.0  2022.0                 DEP              0.207988   
17276   46140.0  2022.0                 DEP              0.207988   
17277   47260.0  2022.0                 DEP              0.207988   
17278   48620.0  2022.0                 DEP              0.207988   
17279   49340.0  2022.0                 DEP              0.207988   

       baseline_moran_p  final_moran_value  final_moran_p  selected_k  \
0                 0.002           0.082131          0.001           0   
1                 0.002           0.082131          0.001           0   
2                 0.002           0.082131          0.001           0   
3                 0.002           0.082131          0.001           0   
4                 0.002           0.082131          0.001           0   
...                 ...                ...            ...         ...   
17275             0.001           0.207988          0.001           0   
17276             0.001           0.207988          0.001           0   
17277             0.001           0.207988          0.001           0   
17278             0.001           0.207988          0.001           0   
17279             0.001           0.207988          0.001           0   

          SSAMI  ln_pop_beta       ln_pop_p  ln_pop_CI_lower  ln_pop_CI_upper  
0      0.400158     0.882118  5.981609e-202         0.839416          0.92482  
1      1.510457     0.882118  5.981609e-202         0.839416          0.92482  
2      0.668788     0.882118  5.981609e-202         0.839416          0.92482  
3     -0.485079     0.882118  5.981609e-202         0.839416          0.92482  
4      0.203467     0.882118  5.981609e-202         0.839416          0.92482  
...         ...          ...            ...              ...              ...  
17275 -0.357817     0.811791  1.654943e-209         0.773672          0.84991  
17276  0.710707     0.811791  1.654943e-209         0.773672          0.84991  
17277  0.027813     0.811791  1.654943e-209         0.773672          0.84991  
17278 -0.047811     0.811791  1.654943e-209         0.773672          0.84991  
17279 -0.725469     0.811791  1.654943e-209         0.773672          0.84991  

[17280 rows x 13 columns]

---

In [ ]:
df3 = pd.read_csv('../00_data/03_analysis_data/all_factor_72_12.csv')

In [ ]:
df

cbsacode  Year              factor  baseline_moran_value  \
0         10740  2011  excessive_drinking              0.298481   
1         11260  2011  excessive_drinking              0.298481   
2         12060  2011  excessive_drinking              0.298481   
3         12260  2011  excessive_drinking              0.298481   
4         12420  2011  excessive_drinking              0.298481   
...         ...   ...                 ...                   ...   
17275     45820  2022           depressed              0.289262   
17276     46140  2022           depressed              0.289262   
17277     47260  2022           depressed              0.289262   
17278     48620  2022           depressed              0.289262   
17279     49340  2022           depressed              0.289262   

       baseline_moran_p  final_moran_value  final_moran_p  selected_k  \
0                 0.001           0.026173          0.126         132   
1                 0.001           0.026173          0.126         132   
2                 0.001           0.026173          0.126         132   
3                 0.001           0.026173          0.126         132   
4                 0.001           0.026173          0.126         132   
...                 ...                ...            ...         ...   
17275             0.001           0.018403          0.194          72   
17276             0.001           0.018403          0.194          72   
17277             0.001           0.018403          0.194          72   
17278             0.001           0.018403          0.194          72   
17279             0.001           0.018403          0.194          72   

          SSAMI  ln_pop_beta  ln_pop_p  ln_pop_CI_lower  ln_pop_CI_upper  \
0     -0.313637     1.005161       0.0         0.988715         1.021607   
1     -0.025590     1.005161       0.0         0.988715         1.021607   
2     -0.057418     1.005161       0.0         0.988715         1.021607   
3     -0.041601     1.005161       0.0         0.988715         1.021607   
4      0.254033     1.005161       0.0         0.988715         1.021607   
...         ...          ...       ...              ...              ...   
17275 -0.006041     0.933195       0.0         0.923049         0.943340   
17276  0.371638     0.933195       0.0         0.923049         0.943340   
17277  0.113171     0.933195       0.0         0.923049         0.943340   
17278  0.000698     0.933195       0.0         0.923049         0.943340   
17279 -0.034701     0.933195       0.0         0.923049         0.943340   

       ln_area_beta  ln_area_p  ln_area_CI_lower  ln_area_CI_upper  
0         -0.004096   0.813785         -0.038220          0.030028  
1         -0.004096   0.813785         -0.038220          0.030028  
2         -0.004096   0.813785         -0.038220          0.030028  
3         -0.004096   0.813785         -0.038220          0.030028  
4         -0.004096   0.813785         -0.038220          0.030028  
...             ...        ...               ...               ...  
17275     -0.032342   0.003506         -0.054023         -0.010662  
17276     -0.032342   0.003506         -0.054023         -0.010662  
17277     -0.032342   0.003506         -0.054023         -0.010662  
17278     -0.032342   0.003506         -0.054023         -0.010662  
17279     -0.032342   0.003506         -0.054023         -0.010662  

[17280 rows x 17 columns]

In [ ]:
import numpy as np
import pandas as pd
import statsmodels.api as sm

def scaling(X, y, ci_vars=None):
    """
    Perform OLS regression of y on X (with intercept). Returns coefficients, 
    confidence intervals, R-squared, and number of observations.

    Parameters:
    - X: DataFrame or Series of predictor(s)
    - y: Series of response variable
    - ci_vars: List of variable names (str) for which to extract 95% CI 
               If None, return CI for all predictors

    Returns:
    - betas: Dictionary of coefficients {var_name: beta}
    - cis: Dictionary of 95% CIs {var_name: (lower, upper)}
    - r_squared: R-squared of the regression
    - n: Number of observations
    """
    if isinstance(X, pd.Series):
        X = X.to_frame()

    X_with_const = sm.add_constant(X)
    model = sm.OLS(y, X_with_const).fit()

    betas = model.params.to_dict()
    conf_int = model.conf_int(alpha=0.05)

    if ci_vars is None:
        ci_vars = X.columns.tolist()
    
    cis = {var: tuple(conf_int.loc[var]) for var in ci_vars if var in conf_int.index}

    return betas, cis, model.rsquared, len(y)

In [ ]:
df

Pair p_value  \
0                Depression, Unhealthy Lifestyle    0.00   
1                Depression, Physical Inactivity    0.00   
2                                Depression, GDP    0.00   
3            Depression, Mental Health Providers    0.72   
4                          Depression, Park Area    0.00   
..                                           ...     ...   
74                               Depression, GDP    0.00   
75                         Depression, Park Area    0.00   
76      Unhealthy Lifestyle, Physical Inactivity    0.00   
77  Unhealthy Lifestyle, Mental Health Providers    0.00   
78                Unhealthy Lifestyle, Park Area    0.00   

                                  Conditional_Factors  
0                                                      
1                                                      
2                                                      
3                                                      
4                                                      
..                                                ...  
74  Unhealthy Lifestyle, Physical Inactivity, Park...  
75      Unhealthy Lifestyle, Physical Inactivity, GDP  
76     Depression, Mental Health Providers, Park Area  
77         Depression, Physical Inactivity, Park Area  
78  Depression, Physical Inactivity, Mental Health...  

[79 rows x 3 columns]